# Finishing the web crawler, last effort!

### The code so far

In [1]:
def fixInternalLink(address,url):
    if url[0:4]=="http":
        return url
    else:
        if url[0:0]=="/" and address[-1]=="/":
            url=address[:-2]+url
        elif  url[0:0]!="/" and address[-1]!="/":
            url=address+"/"+url
        else:
            url=address+url
        return url

            
def getLink(p,n): # this function gets the first link in p starting from position n, adjusted to deal with single quotations
    startPosition1=p.find('href="',n)
    startPosition2=p.find("href=\\'",n)
    if startPosition1>-1 and (startPosition2==-1 or startPosition1<startPosition2):
        startPosition=startPosition1+6
        endPosition=p.find('"',startPosition)-1
        url=p[startPosition:endPosition+1]
        return endPosition,url
    elif startPosition2>-1 and (startPosition1==-1 or startPosition2<startPosition1):
        startPosition=startPosition2+7
        endPosition=p.find("\\'",startPosition)-1
        url=p[startPosition:endPosition+1]
        return endPosition,url
    else:
        return -1,""


import requests
from hashlib import sha256 # do not forget this, or you won't have sha256 available
limitVisitedPages=200
depthLimit=5
Crawled=[]
Skipped=[]
skippedEqual=[]
visitedHashes=[]
toCrawl=["http://www.paolocoletti.it/test"]
toCrawlWithDepth=[["http://www.paolocoletti.it/test",1]] # new structure with URL and depth
BadExtensions=[".png",".gif",".jpeg",".jpg",".php",".json",".ico","#"]

while len(toCrawl)>0 and len(Crawled)<limitVisitedPages: 
    pageAddress,depth = toCrawlWithDepth.pop(0) # pay attention that now I pop out the url and the depth
    toCrawl.pop(0) 
    page = requests.get(pageAddress) 
    sha=sha256(page.content).hexdigest()
    if sha in visitedHashes:
        skippedEqual.append(pageAddress)
    else:
        visitedHashes.append(sha)
        print("I am crawling page: " + pageAddress) # I put this to have an idea of what the program is doing
        Crawled.append(pageAddress)

        n=0
        while n>=0:
            n,url=getLink(str(page.content),n+1)
            if n>-1 and url!="":
                url=fixInternalLink(pageAddress,url)
                if url[-1:] not in BadExtensions and url[-4:] not in BadExtensions and url[-5:] not in BadExtensions: # otherwise we completely forget about it
                    if url not in toCrawl and url not in Crawled:
                        if depth<depthLimit:
                            toCrawlWithDepth.append([url,depth+1]) # if the depth of the current page is below the limit, I add it to the list
                            toCrawl.append(url) 
                        elif depth==depthLimit:
                            if url not in Skipped:
                                Skipped.append(url) # otherwise if the depth of the current page is AT THE LIMIT, then the link is beyond the limit and I add it to the list of the Skipped
                        else:
                            print("Error: what am I doing here????") # it should never happen that the depth of this page is above the limit!
                    
print(len(Crawled),len(toCrawl),len(Skipped))
print(Crawled)
print(toCrawl)
print(Skipped)
print(skippedEqual)

I am crawling page: http://www.paolocoletti.it/test
I am crawling page: http://www.paolocoletti.it/test/test2.html
I am crawling page: http://www.paolocoletti.it/test/test3.html
I am crawling page: http://www.paolocoletti.it/test/test4.html
4 0 0
['http://www.paolocoletti.it/test', 'http://www.paolocoletti.it/test/test2.html', 'http://www.paolocoletti.it/test/test3.html', 'http://www.paolocoletti.it/test/test4.html']
[]
[]
['http://www.paolocoletti.it/test/test.html']


## Indexing the content

Our last effort!

Until now we have built a perfect crawler which, however, is good only at retrieving links. We would like also to associate search terms with those links.

First of all, we need to remove all the tags from the web page, i.e. all the things such as <whatever....>, because these are not words which appear on the web page but only technical information. Thus we build together a function which does it.

In [1]:
def removeTags(s):
    # returns a string equal to s but without all the tags
    i=0
    r=""
    while i<len(s):
        if s[i]!="<":
            r=r+s[i]
        else:
            while i<len(s) and s[i]!=">":
                i=i+1
            # at this point i is on the ">" symbol
            # just to avoid having a word attached to another when there is a tag in the middle, such as Paolo<...>Coletti -> PaoloColetti, we introduce a space here
            r=r+" "
        i=i+1
    return r

print(removeTags('<!DOCTYPE html PUBLIC "-//W3C//DTD HTML 4.01 Transitional//EN" "http://www.w3.org/TR/1999/REC-html401-19991224/loose.dtd"><html><head><title>Test 4 web page</title></head><body><h1>Test 4</h1><p>Dice, dire, duty, dividend, desire, destroy</p><p>This is just test web page numer four. Here <a href="http://www.paolocoletti.it/test/test.html">a BACK link to test original page</a>.</p><p>Here <a href="http://www.paolocoletti.it/test/test3.html">another link to test 3</a>.</p></body></html>'))

    Test 4 web page    Test 4  Dice, dire, duty, dividend, desire, destroy  This is just test web page numer four. Here  a BACK link to test original page .  Here  another link to test 3 .   


Now that we have a clean text we can use the function splitString, built some time ago, to get all the words of the page as a list. I paste here the old function for your convenience.

In [2]:
def splitString(s):
    Ortho=[" ",";",".","!","?",":",",","-"]
    L=[]
    if len(s)==0: # you never know....
        return L
    current=0
    start=0
    # first of all I skip all the starting ortho symbols
    while current < len(s) and s[current] in Ortho: 
        current=current+1
    start=current
    # now we are sure that start and current are at the beginning of the first real word (or that the string is over)
    while current < len(s):
        if s[current] in Ortho:
            # I found an orthograhic symbol. 
            # first I append the word from start up tu current-1
            L.append(s[start:current])
            # But there might be several symbols, so I go on until I find a non-orthographic symbol or until the string is over
            while current < len(s) and s[current] in Ortho:
                current=current+1
            # now current is on the first non-ortho symbol
            start=current # and thus start is set equal to current, as we will have to re-start the function.
        else:
            current=current+1
    # I am now outside the loop. I might be outside because the last character is an orthographic symbol and in this case fine!
    # but I might be outside because the string ended with a letter and thus I am still "inside" a word! And I have to add it
    if s[-1] not in Ortho:
        L.append(s[start:])
    return L

Using the two function in combination, we can get easily the list of words.

In [3]:
print(splitString(removeTags('<!DOCTYPE html PUBLIC "-//W3C//DTD HTML 4.01 Transitional//EN" "http://www.w3.org/TR/1999/REC-html401-19991224/loose.dtd"><html><head><title>Test 4 web page</title></head><body><h1>Test 4</h1><p>Dice, dire, duty, dividend, desire, destroy</p><p>This is just test web page numer four. Here <a href="http://www.paolocoletti.it/test/test.html">a BACK link to test original page</a>.</p><p>Here <a href="http://www.paolocoletti.it/test/test3.html">another link to test 3</a>.</p></body></html>')))

['Test', '4', 'web', 'page', 'Test', '4', 'Dice', 'dire', 'duty', 'dividend', 'desire', 'destroy', 'This', 'is', 'just', 'test', 'web', 'page', 'numer', 'four', 'Here', 'a', 'BACK', 'link', 'to', 'test', 'original', 'page', 'Here', 'another', 'link', 'to', 'test', '3']


And now the final effort! Modify the previous program adding a dict **words** which associates each word with a list of the links in which that word is found. E.g. if word "Test" is found in three different webpage, words["Test"] will contain as value a list with those three links.

Go on to exe file...